In [ ]:
import simtool as st
import numpy as np
import plotly.graph_objects as go
import ipywidgets as w
import math

In [ ]:
simToolName = "st4pnjunction"

In [ ]:
# get the list of inputs for the simtool.
nb = st.utils.searchForSimTool(simToolName)

In [ ]:
inputs = st.utils.getSimToolInputs(nb)

In [ ]:
outputs = st.utils.getSimToolOutputs(nb)
#outputs

In [ ]:
r = st.Run(nb, inputs)

In [ ]:
OutputLog = r.read('Output Log')
Parameters = r.read('Parameters')
Efn = r.read('Efn')
Efp = r.read('Efp')
HoleDensity = r.read('Hole Density')
ElectronDensity = r.read('Electron Density')
EquilibriumHoleDensity = r.read('Equilibrium Hole Density')
EquilibriumElectronDensity = r.read('Equilibrium Electron Density')
ChargeDensity = r.read('Charge Density')
NetChargeDensity = r.read('Net Charge Density')
EquilibriumEi = r.read('Equilibrium Ei')
Ei = r.read('Ei')
EquilibriumPotential = r.read('Equilibrium Potential')
EquilibriumEc = r.read('Equilibrium Ec')
Ec = r.read('Ec')
EquilibriumEv = r.read('Equilibrium Ev')
Ev = r.read('Ev')
EquilibriumElectricField = r.read('Equilibrium Electric Field')
ElectricField = r.read('Electric Field')
EquilibriumRecombinationRate = r.read('Equilibrium Recombination Rate')
RecombinationRate = r.read('Recombination Rate') 
CVCharacteristic = r.read('CV Characteristic')
IVCharacteristic = r.read('IV Characteristic')
QuasiFermiElectrons = r.read('QuasiFermi Electrons')
QuasiFermiHoles = r.read('QuasiFermi Holes')
TotalCurrentHoles = r.read('Total Current Holes')
TotalCurrentElectrons = r.read('Total Current Electrons')
TotalCurrent = r.read('Total Current')
ExcessElectronDensity = r.read('Excess Electron Density')
ExcessHoleDensity = r.read('Excess Hole Density')
EquilibriumNetChargeDensity = r.read('Equilibrium Net Charge Density')
ElectrostaticPotential = r.read('Electrostatic Potential')
wchildren = [w.Box() for i in range(17)]

In [ ]:
def FunctionApproximation(fnc, mname, T, lp, li, ln, na, nd, dda_x):
    data = {"position":[], "function":[]}
    if mname == "Si" and li == 0 :
        Kb = 1.38E-23
        q = 1.602E-19
        eps0 = 8.85E-12
        eps = 11.8*eps0
        NA = na*1e6
        ND = nd*1e6
        VT = Kb*T/q
        Ni = 1e+16
        Vbi = VT*math.log(NA*ND/Ni/Ni)
        Wn = math.sqrt(2*eps*NA*Vbi/q/ND/(NA+ND))
        Wp = math.sqrt(2*eps*ND*Vbi/q/NA/(NA+ND))
        xj = lp*1e-6
        W = 1e-6*(lp+ln)
        
        for x in dda_x:
            xxx = x*1e-6
            if xxx < xj - Wp:
                data['position'].append(x)
                data['function'].append(0)

            if xxx > xj - Wp and xxx < xj:
                    data['position'].append(x)
                    if fnc == "Potential":
                        data['function'].append(q*NA/2/eps*pow(Wp+xxx-xj,2))
                    elif fnc == "ElectricField":
                        data['function'].append(1e-2*-q*NA/eps*(Wp+xxx-xj))
                    elif fnc == "Charge":
                        data['function'].append(1e-6*-q*NA)
                    else:
                        data['function'].append(0)
                    
            if xxx > xj and xxx < xj+Wn:
                    data['position'].append(x)
                    if fnc == "Potential":
                        data['function'].append(Vbi-q*ND/2/eps*pow(xxx-xj-Wn,2))
                    elif fnc == "ElectricField":
                        data['function'].append(1e-2*q*ND/eps*(xxx-xj-Wn))
                    elif fnc == "Charge":
                        data['function'].append(1e-6*q*ND)
                    else:
                        data['function'].append(0)

            if xxx > xj + Wn:
                data['position'].append(x)
                if fnc == "Potential":
                    data['function'].append(Vbi)
                else:
                    data['function'].append(0)
    return data

def createSequence(data):
    play = w.Play(
        value=0,
        min=0,
        max=len(data)-1,
        step=1,
        description="Press play",
    )
    slider = w.IntSlider(
        min=0,
        max=len(data)-1,
    )
    plot = go.FigureWidget(data=data[0]['data'], layout=data[0]['layout'])
    w.jslink((play, 'value'), (slider, 'value'))
    slider.observe(lambda change, f=data, p=plot : p.update(data=f[change["new"]]['data'], layout=f[change["new"]]['layout'], overwrite=True), names="value")
    sequence = w.VBox([ 
        plot,
        w.HBox([play, slider])
    ])
    return sequence

In [ ]:
traces=[]
traces.append({
    'type':'scatter',
    'name':'efn',
    'x': Efn['position'],
    'y': Efn['function'],
})
traces.append({
    'type':'scatter',
    'name':'efp',
    'x': Efp['position'],
    'y': Efp['function'],
})

traces.append({
    'type':'scatter',
    'name':'Ec',
    'x': EquilibriumEc['position'],
    'y': EquilibriumEc['function'],
})
traces.append({
    'type':'scatter',
    'name':'Ev',
    'x': EquilibriumEv['position'],
    'y': EquilibriumEv['function'],
})
traces.append({
    'type':'scatter',
    'name':'Ei',
    'x': EquilibriumEi['position'],
    'y': EquilibriumEi['function'],
})
layout = {
    'title' : 'Energy Band Diagram at Equilibriunm',
}
wchildren[0] = go.FigureWidget(data=traces, layout=layout)
#wchildren[0]

In [ ]:
traces=[]
traces.append({
    'type':'scatter',
    'name':'Holes',
    'x': EquilibriumHoleDensity['position'],
    'y': EquilibriumHoleDensity['function'],
})
traces.append({
    'type':'scatter',
    'name':'Electrons',
    'x': EquilibriumElectronDensity['position'],
    'y': EquilibriumElectronDensity['function'],
})
traces.append({
    'type':'scatter',
    'name':'Charge Density',
    'x': ChargeDensity['position'],
    'y': ChargeDensity['function'],
})
layout = {
    'title' : 'Density for holes/electrons at equilibrium',
    'yaxis' : {'type':'log'}
}
wchildren[1] = go.FigureWidget(data=traces, layout=layout)
#wchildren[1]

In [ ]:
ChargeDensityApproximation = FunctionApproximation(
    "Charge", 
    inputs.materialp.value, 
    inputs.temperature.value, 
    inputs.p_len.value, 
    inputs.i_len.value, 
    inputs.n_len.value, 
    inputs.Na.value, 
    inputs.Nd.value, 
    EquilibriumNetChargeDensity["position"]
)
traces=[]
traces.append({
    'type':'scatter',
    'name':'Approximation',
    'x': ChargeDensityApproximation['position'],
    'y': ChargeDensityApproximation['function'],
})
traces.append({
    'type':'scatter',
    'name':'Net Charge Density',
    'x': EquilibriumNetChargeDensity['position'],
    'y': EquilibriumNetChargeDensity['function'],
})
layout = {
    'title' : '',
}
wchildren[2] = go.FigureWidget(data=traces, layout=layout)
#wchildren[2]

In [ ]:
EquilibriumPotentialApproximation = FunctionApproximation(
    "Potential", 
    inputs.materialp.value, 
    inputs.temperature.value, 
    inputs.p_len.value, 
    inputs.i_len.value, 
    inputs.n_len.value, 
    inputs.Na.value, 
    inputs.Nd.value, 
    EquilibriumPotential["position"]
)
traces=[]
traces.append({
    'type':'scatter',
    'name':'Approximation',
    'x': EquilibriumPotentialApproximation['position'],
    'y': EquilibriumPotentialApproximation['function'],
})
traces.append({
    'type':'scatter',
    'name':'Electrostatic Potential',
    'x': EquilibriumPotential['position'],
    'y': EquilibriumPotential['delta'],
})
layout = {
    'title' : '',
}
wchildren[3] = go.FigureWidget(data=traces, layout=layout)
#wchildren[3]

In [ ]:
EquilibriumFieldApproximation = FunctionApproximation(
    "ElectricField", 
    inputs.materialp.value, 
    inputs.temperature.value, 
    inputs.p_len.value, 
    inputs.i_len.value, 
    inputs.n_len.value, 
    inputs.Na.value, 
    inputs.Nd.value, 
    EquilibriumElectricField["position"]
)
traces=[]
traces.append({
    'type':'scatter',
    'name':'Approximation',
    'x': EquilibriumFieldApproximation['position'],
    'y': EquilibriumFieldApproximation['function'],
})
traces.append({
    'type':'scatter',
    'name':'Electric Field',
    'x': EquilibriumElectricField['position'],
    'y': EquilibriumElectricField['function'],
})
layout = {
    'title' : '',
}
wchildren[4] = go.FigureWidget(data=traces, layout=layout)
#wchildren[4]

In [ ]:
traces=[]
traces.append({
    'type':'scatter',
    'name':'CV Characteristics',
    'x': CVCharacteristic['voltage'],
    'y': CVCharacteristic['function'],
})
layout = {
    'title' : '',
}
wchildren[5] = go.FigureWidget(data=traces, layout=layout)
#wchildren[5]

In [ ]:
traces=[]
traces.append({
    'type':'scatter',
    'name':'IV Characteristics',
    'x': IVCharacteristic['voltage'],
    'y': IVCharacteristic['function'],
})
layout = {
    'title' : '',
}
wchildren[6] = go.FigureWidget(data=traces, layout=layout)
#wchildren[6]

In [ ]:
frames=[]
for k in Ec.keys():
    traces = []
    traces.append({
        'type':'scatter',
        'name':'efn',
        'x': QuasiFermiElectrons[k]['position'],
        'y': QuasiFermiElectrons[k]['function'],
    })
    traces.append({
        'type':'scatter',
        'name':'efp',
        'x': QuasiFermiHoles[k]['position'],
        'y': QuasiFermiHoles[k]['function'],
    })
    traces.append({
        'type':'scatter',
        'name':'Ec',
        'x': Ec[k]['position'],
        'y': Ec[k]['function'],
    })
    traces.append({
        'type':'scatter',
        'name':'Ei',
        'x': Ei[k]['position'],
        'y': Ei[k]['function'],
    })    
    traces.append({
        'type':'scatter',
        'name':'Ev',
        'x': Ev[k]['position'],
        'y': Ev[k]['function'],
    })
    layout = {
        'title' : 'Energy Band Diagram at Bias ' + k,
    }
    frames.append({"data": traces, "layout": layout, "name": str(k)})


wchildren[7] = createSequence(frames)
#wchildren[7]

In [ ]:
frames=[]
for k in Ec.keys():
    traces = []
    traces.append({
        'type':'scatter',
        'name':'Jn - Hole current density',
        'x': TotalCurrentHoles[k]['position'],
        'y': TotalCurrentHoles[k]['function'],
    })
    traces.append({
        'type':'scatter',
        'name':'Jn - Electron current density',
        'x': TotalCurrentElectrons[k]['position'],
        'y': TotalCurrentElectrons[k]['function'],
    })
    traces.append({
        'type':'scatter',
        'name':'J - Total current density',
        'x': TotalCurrent[k]['position'],
        'y': TotalCurrent[k]['function'],
    })
    layout = {
        'title' : 'Bias point ' + k,
        'yaxis' : {'type':'log'},
        'legend' : {'xanchor' : 'center','x': 0.5, 'y':-0.4}
    }
    frames.append({"data": traces, "layout": layout, "name": str(k)})


wchildren[8] = createSequence(frames)
#wchildren[8]

In [ ]:
frames=[]
for k in Ec.keys():
    traces = []
    traces.append({
        'type':'scatter',
        'name':'Holes',
        'x': HoleDensity[k]['position'],
        'y': HoleDensity[k]['function'],
    })
    traces.append({
        'type':'scatter',
        'name':'Electrons',
        'x': ElectronDensity[k]['position'],
        'y': ElectronDensity[k]['function'],
    })
    traces.append({
        'type':'scatter',
        'name':'Charge Density',
        'x': ChargeDensity['position'],
        'y': ChargeDensity['function'],
    })
    layout = {
        'title' : 'Bias point ' + k,
        'yaxis' : {'type':'log'},
        'legend' : {'xanchor' : 'center','x': 0.5, 'y':-0.4}
    }
    frames.append({"data": traces, "layout": layout, "name": str(k)})
    
wchildren[9] = createSequence(frames)
#wchildren[9]

In [ ]:
frames=[]
for k in Ec.keys():
    traces = []
    traces.append({
        'type':'scatter',
        'name':'Electron Density',
        'x': ExcessElectronDensity[k]['position'],
        'y': ExcessElectronDensity[k]['function'],
    })
    traces.append({
        'type':'scatter',
        'name':'Hole Density',
        'x': ExcessHoleDensity[k]['position'],
        'y': ExcessHoleDensity[k]['function'],
    })
    layout = {
        'title' : 'Bias point ' + k,
        'yaxis' : {'type':'log'},
    }

    frames.append({"data": traces, "layout": layout, "name": str(k)})
    
wchildren[10] = createSequence(frames[1:])
#wchildren[10]

In [ ]:
frames=[]
for k in Ec.keys():
    traces = []
    traces.append({
        'type':'scatter',
        'name':'Electron Density',
        'x': NetChargeDensity[k]['position'],
        'y': NetChargeDensity[k]['function'],
    })

    layout = {
        'title' : 'Bias point ' + k,
    }

    frames.append({"data": traces, "layout": layout, "name": str(k)})
    
wchildren[11] = createSequence(frames)
#wchildren[11]

In [ ]:
frames=[]
for k in Ec.keys():
    traces = []
    traces.append({
        'type':'scatter',
        'name':'Electrostatic Potential',
        'x': ElectrostaticPotential[k]['position'],
        'y': ElectrostaticPotential[k]['delta'],
    })

    layout = {
        'title' : 'Bias point ' + k,
    }

    frames.append({"data": traces, "layout": layout, "name": str(k)})
    
wchildren[12] = createSequence(frames)
#wchildren[12]

In [ ]:
frames=[]
for k in Ec.keys():
    traces = []
    traces.append({
        'type':'scatter',
        'name':'Electric Field',
        'x': ElectricField[k]['position'],
        'y': ElectricField[k]['function'],
    })

    layout = {
        'title' : 'Bias point ' + k,
    }

    frames.append({"data": traces, "layout": layout, "name": str(k)})
    
wchildren[13] = createSequence(frames)
#wchildren[13]

In [ ]:
frames=[]
for k in Ec.keys():
    traces = []
    traces.append({
        'type':'scatter',
        'name':'Recombination Rate',
        'x': RecombinationRate[k]['position'],
        'y': RecombinationRate[k]['function'],
    })

    layout = {
        'title' : 'Bias point ' + k,
        'yaxis' : {'type':'log'},
    }

    frames.append({"data": traces, "layout": layout, "name": str(k)})
    
wchildren[14] = createSequence(frames)
#wchildren[14]

In [ ]:
wchildren[15] = w.Output()
with wchildren[15]:
    print(Parameters)

In [ ]:
wchildren[16] = w.Output()
with wchildren[16]:
    print(OutputLog)

In [ ]:
accordion = w.Accordion(children=wchildren)
accordion.set_title(0, 'Energy Band Diagram (at equilibrim)')
accordion.set_title(1, 'Doping Electron and Hole Density (at equilibrium)')
accordion.set_title(2, 'Net Charge Density (at equilibrium)')
accordion.set_title(3, 'Electrostratic Potential (at Equilibriun)')
accordion.set_title(4, 'Electric Field (at equilibriumn)')
accordion.set_title(5, 'C-V Characteristics')
accordion.set_title(6, 'I-V Characteristics')
accordion.set_title(7, 'Energy Band Diagram (at applied bias)')
accordion.set_title(8, 'Total Electron and Hole (at applied bias)')
accordion.set_title(9, 'Doping Electron and Hole Density (at applied bias)')
accordion.set_title(10, 'Excess Carrier Density (at applied bias)')
accordion.set_title(11, 'Net Charge Density (at applied bias)')
accordion.set_title(12, 'Electrostatic Potential (at applied bias)')
accordion.set_title(13, 'Electric Field (at applied bias)')
accordion.set_title(14, 'Recombination Rate (at applied bias)')
accordion.set_title(15, 'Input Parameters')
accordion.set_title(16, 'Output Log')
accordion